In [1]:
# Load LSTM network and generate text
import sys
import numpy

from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Dropout
from keras.layers import LSTM
from keras.callbacks import ModelCheckpoint
from keras.utils import np_utils

# load ascii text and covert to lowercase


Using TensorFlow backend.


In [3]:
filename = 'all_lyrics_no-umlaut_edited2.txt'


raw_text = open(filename).read()
raw_text = raw_text.lower()

raw_text = raw_text.replace('\x99', '')
raw_text = raw_text.replace('\x80', '')
raw_text = raw_text.replace('\xe2', '')

raw_text = raw_text.replace('"', '')
raw_text = raw_text.replace('(', '')
raw_text = raw_text.replace(')', '')



# create mapping of unique chars to integers, and a reverse mapping
chars = sorted(list(set(raw_text)))
char_to_int = dict((c, i) for i, c in enumerate(chars))
int_to_char = dict((i, c) for i, c in enumerate(chars))
# summarize the loaded data
n_chars = len(raw_text)
n_vocab = len(chars)
print("Total Characters: ", n_chars)
print("Total Vocab: ", n_vocab)


('Total Characters: ', 149347)
('Total Vocab: ', 49)


In [4]:

# prepare the dataset of input to output pairs encoded as integers
seq_length = 100
dataX = []
dataY = []
for i in range(0, n_chars - seq_length, 1):
	seq_in = raw_text[i:i + seq_length]
	seq_out = raw_text[i + seq_length]
	dataX.append([char_to_int[char] for char in seq_in])
	dataY.append(char_to_int[seq_out])
n_patterns = len(dataX)
print("Total Patterns: ", n_patterns)
# reshape X to be [samples, time steps, features]
X = numpy.reshape(dataX, (n_patterns, seq_length, 1))
# normalize
X = X / float(n_vocab)
# one hot encode the output variable
y = np_utils.to_categorical(dataY)
# define the LSTM model
model = Sequential()
model.add(LSTM(128, input_shape=(X.shape[1], X.shape[2])))
model.add(Dense(y.shape[1], activation='softmax'))

model.compile(loss='categorical_crossentropy', optimizer='rmsprop')


('Total Patterns: ', 149247)


In [ ]:
#filename = "aws_128_0.0_char_weights-improvement-149-1.5761.hdf5"
#model.load_weights(filename)

# define the checkpoint
filepath="aws_128_0.0_batch32_char_weights-improvement-{epoch:02d}-{loss:.4f}.hdf5"
checkpoint = ModelCheckpoint(filepath, monitor='loss', verbose=1, save_best_only=True, mode='min')
callbacks_list = [checkpoint]

model.fit(X, y, epochs=20, batch_size=32, callbacks=callbacks_list)



Epoch 1/20
149247/149247 [==============================] - 889s - loss: 1.7697   
Epoch 2/20
149247/149247 [==============================] - 889s - loss: 1.7970   
Epoch 3/20
149247/149247 [==============================] - 882s - loss: 1.8084   
Epoch 4/20
149247/149247 [==============================] - 883s - loss: 1.7935   
Epoch 5/20
149247/149247 [==============================] - 884s - loss: 1.7947   
Epoch 6/20
149247/149247 [==============================] - 882s - loss: 1.7969   
Epoch 7/20
149247/149247 [==============================] - 881s - loss: 1.8000   
Epoch 8/20
  7712/149247 [>.............................] - ETA: 843s - loss: 1.7680 

In [5]:

def sample(preds, temperature=1.0):
    # helper function to sample an index from a probability array
    preds = numpy.asarray(preds).astype('float64')
    preds = numpy.log(preds) / temperature
    exp_preds = numpy.exp(preds)
    preds = exp_preds / numpy.sum(exp_preds)
    probas = numpy.random.multinomial(1, preds, 1)
    return numpy.argmax(probas)



In [11]:
filename = "aws_128_0.0_char_weights-improvement-149-1.5761.hdf5"
model.load_weights(filename)


# pick a random seed
start = numpy.random.randint(0, len(dataX)-1)
pattern = dataX[start]
print("Seed:")
print("\"", ''.join([int_to_char[value] for value in pattern]), "\"")


for temprt in [0.1, 0.2, 0.5, 1.0]:
    print("--> \n temp = ", temprt, "\n <--")
# generate characters
    for i in range(200):
        x = numpy.reshape(pattern, (1, len(pattern), 1))
        x = x / float(n_vocab)
        prediction = model.predict(x, verbose=0)
        #index = numpy.argmax(prediction)
        index = sample(numpy.squeeze(prediction), temprt)
        result = int_to_char[index]
        seq_in = [int_to_char[value] for value in pattern]
        sys.stdout.write(result)
        pattern.append(index)
        pattern = pattern[1:len(pattern)]
print("\nDone.")



model.load_weights(filename)


pattern = dataX[start]


print("-->> ArgMax() <<--")
# generate characters
for i in range(200):
    x = numpy.reshape(pattern, (1, len(pattern), 1))
    x = x / float(n_vocab)
    prediction = model.predict(x, verbose=0)
    index = numpy.argmax(prediction)
    #index = sample(numpy.squeeze(prediction), temprt)
    result = int_to_char[index]
    seq_in = [int_to_char[value] for value in pattern]
    sys.stdout.write(result)
    pattern.append(index)
    pattern = pattern[1:len(pattern)]
print("\nDone.")


Seed:
('"', "k in my eyes, sharona\r\nkeep a little mystery, kissin' me\r\nrunnin' down the length of my thigh, sharo", '"')
('--> \n temp = ', 0.1, '\n <--')
na
wou knot is 

/Users/mfrey/anaconda/envs/py27/lib/python2.7/site-packages/ipykernel_launcher.py:5: RuntimeWarning: divide by zero encountered in log
  """


roeer tee pacs fu soilt teeet 
i mose mak wou b srite toie, 
i cn lot an aaoptin tom
o tank toe b steked 
i want you bn me you
i don't care
i don't care
i don't care
('--> \n temp = ', 0.2, '\n <--')

i don't care
i don't care
i don't care
i don't care
i don't care
i don't care
i don't care
i don't care
i don't care
i don't care
i don't care
i don't care
i don't care
i don't care
i d('--> \n temp = ', 0.5, '\n <--')
on't care
i don't want you... 

i cin't bare ata i mrnwd 
you bod tuu ar a birle oote
i don't kake au aal sodat foy 
i want you b bmy myohld
boyyo hotnhng to tae.
io's go norua meset a gool('--> \n temp = ', 1.0, '\n <--')
n cacklt
wher gs uoe crpv

fntiy rhel ase baad st yee
wr drvhen, los,o net oek toiob.
siw 
gom whene yourg, a weeplc woth
shdt gtn tometpddg iis, 
glsuie hike and lu'e hlysrrnngg?ger pwtii,h bo
Done.
-->> ArgMax() <<--


ValueError: Error when checking : expected lstm_1_input to have shape (None, 100, 1) but got array with shape (1, 101, 1)

In [31]:
for ii in range(len(dataX[0])):
    print(int_to_char[dataX[0][ii]])

w
h
e
n
 
i
'
m
 
l
y
i
n
'
 
i
n
 
m
y
 
b
e
d
 
a
t
 
n
i
g
h
t



i
 
d
o
n
'
t
 
w
a
n
n
a
 
g
r
o
w
 
u
p



n
o
t
h
i
n
g
 
e
v
e
r
 
s
e
e
m
s
 
t
o
 
t
u
r
n
 
o
u
t
 
r
i
g
h
t



i
 
d
o
